In [1]:
import glob
import random
import os
import numpy as np 
from scipy import ndimage as ndi
import matplotlib
import matplotlib.pyplot as plt
import scipy.misc 
import tensorflow as tf
import numpy as np
import scipy.io
import cygan
from tensorflow.keras import layers
import tensorflow_addons as tfa

In [2]:
os.environ["CUDA_VISIBLE_DEVICES"] = "1"

from tensorflow.python.client import device_lib
print(device_lib.list_local_devices())

[name: "/device:CPU:0"
device_type: "CPU"
memory_limit: 268435456
locality {
}
incarnation: 7858598328696432621
, name: "/device:GPU:0"
device_type: "GPU"
memory_limit: 31139201024
locality {
  bus_id: 2
  numa_node: 1
  links {
  }
}
incarnation: 5196476911389310245
physical_device_desc: "device: 0, name: Tesla V100-PCIE-32GB, pci bus id: 0000:af:00.0, compute capability: 7.0"
]


In [4]:
#ORAL CANCER 5 fold validation
import os
import cv2




path = '/home/auser04/Oral_cancer/'

can = [cv2.resize(cv2.imread(path + 'cancer/' +s),dsize = (224,224), interpolation=cv2.INTER_CUBIC) for s in os.listdir(path+'cancer')if ".jpg" or ".jpeg"in s.lower()]
nor = [cv2.resize(cv2.imread(path + 'normal/' +s), dsize = (224,224), interpolation=cv2.INTER_CUBIC) for s in os.listdir(path+'normal')if ".jpg"in s.lower()]

can = (np.array(can)-127.5)/127.5
nor = (np.array(nor)-127.5)/127.5
allCAN = np.concatenate((CAN,can,CAN,can),axis=0)
allNOR = np.concatenate((NOR,nor,NOR[0:2],NOR,nor),axis=0)
res_x = np.append(allNOR,allCAN,axis=0)
print(res_x.shape,allCAN.shape,allNOR.shape)
#NOR10 CAN38

(196, 224, 224, 3) (148, 224, 224, 3) (48, 224, 224, 3)


In [5]:
from __future__ import print_function, division
import keras
from keras.datasets import mnist
from keras.applications import VGG19
from keras.applications import VGG16
from tensorflow.keras.preprocessing import image
from tensorflow.keras.applications.vgg19 import preprocess_input
from tensorflow.keras.layers import Input, Dense, Reshape, Flatten, Dropout, multiply, Add, Concatenate, MaxPool2D
from tensorflow.keras.layers import BatchNormalization, Activation, Embedding, ZeroPadding2D
from tensorflow.keras.layers import LeakyReLU
# from keras_contrib.layers.normalization.instancenormalization import InstanceNormalization
from tensorflow.keras.layers import UpSampling2D, Conv2D, Conv2DTranspose
from tensorflow.keras.models import Sequential, Model
from tensorflow.keras.optimizers import Adam, RMSprop
import tensorflow.keras.backend as K
import matplotlib.pyplot as plt
import tensorflow as tf
import numpy as np
K.clear_session()
class GAN():
    def __init__(self):
        self.img_rows = 224
        self.img_cols = 224
        self.channels = 3
        self.img_shape = (self.img_rows, self.img_cols, self.channels)
        self.latent_dim = 100

#         optimizer = Adam(0.0002, 0.5)
        self.n_critic = 5
        self.clip_value = 0.01
        optimizer = RMSprop(lr=0.00005)
        
        patch = int(self.img_rows / 2**4)
        self.disc_patch = (patch, patch, 1)
        self.gf = 32
        self.df = 64
        
        # Build and compile the discriminator
        self.discriminator_NOR = self.build_discriminator()
        self.discriminator_NOR.compile(loss='mse',
            optimizer=optimizer,
            metrics=['accuracy'])
        
        self.discriminator_CAN = self.build_discriminator()
        self.discriminator_CAN.compile(loss='mse',
            optimizer=optimizer,
            metrics=['accuracy'])
        
        # Build the generator
        self.generator = self.build_encoder()
        print(self.generator.summary())
        #keras.utils.plot_model(self.generator, "generator.png", show_shapes=True)

        
        z = Input(shape=self.img_shape)
        img_source = Input(shape = self.img_shape)
        #img = self.generator([z,img_source])\
        img = self.generator(z)

        # For the combined model we will only train the generator
        self.discriminator_CAN.trainable = False
        self.discriminator_NOR.trainable = False
        # The discriminator takes generated images as input and determines validity
        validity_CAN = self.discriminator_CAN(img)
        validity_NOR = self.discriminator_NOR(img)
        
        
        # The combined model  (stacked generator and discriminator)
        # Trains the generator to fool the discriminator
        self.combined = Model(z,[validity_NOR,validity_CAN])
        self.combined.compile(loss=['binary_crossentropy','mse'],loss_weights=[0,1], optimizer=optimizer)#tf.keras.losses.MeanAbsoluteError
        #keras.utils.plot_model(self.combined, "combined.png", show_shapes=True)

    def wasserstein_loss(self, y_true, y_pred):
        return K.mean(y_true * y_pred)
    
    def build_encoder(self):
        model = cygan.get_resnet_generator(res = 224,name='en')
        load_status = model.load_weights("ae_wgen")#"ae_wgen_new_cancer")
        encoder = model
        #encoder = Model(inputs = model.input, outputs = model.get_layer('add_8').output)
#         model = keras.models.load_model('/home/auser04/0428_oral.h5')
#         encoder = Model(inputs = model.input, outputs = model.get_layer('activation_4').output)
        
        
        
        return encoder
    
        

    
    def build_discriminator(self):
       
        def d_layer(layer_input, filters, f_size=7, normalization=False):
            """Discriminator layer"""
            d = Conv2D(filters, kernel_size=f_size, strides=2, padding='same')(layer_input)
            d = LeakyReLU(alpha=0.2)(d)
#             d = BatchNormalization(momentum=0.8)(d)
            if normalization:
                d = tfa.layers.InstanceNormalization(gamma_initializer=cygan.gamma_init)(d)
            return d

        img = Input(shape=self.img_shape)

        d1 = d_layer(img, self.df, normalization=False)
        d2 = d_layer(d1, self.df*2)
        d3 = d_layer(d2, self.df*4)
        d4 = d_layer(d3, self.df*8)
        validity = Conv2D(1, kernel_size=7, strides=1, padding='same')(d4)

        return Model(img, validity)


    def train(self, epochs, batch_size=128, sample_interval=50, thre = 0.5):

        valid = np.ones((batch_size,) + self.disc_patch)
        fake = np.zeros((batch_size,) + self.disc_patch)
        self.encoder = self.build_encoder()
        for i in range(100):
            idx_NOR = np.random.randint(0, NOR.shape[0], batch_size)
            idx_CAN = np.random.randint(0, CAN.shape[0], batch_size)
            N_imgs = NOR[idx_NOR]
            C_imgs = CAN[idx_CAN]
            self.discriminator_NOR.train_on_batch(N_imgs, valid)
            self.discriminator_NOR.train_on_batch(C_imgs, fake)

        for epoch in range(epochs):

            # ---------------------
            #  Train Discriminator
            # ---------------------

            for _ in range(1):
                idx_NOR = np.random.randint(0, NOR.shape[0], batch_size)
                idx_CAN = np.random.randint(0, CAN.shape[0], batch_size)
                N_imgs = NOR[idx_NOR]
                C_imgs = CAN[idx_CAN]
                gen_imgs = self.generator.predict(C_imgs)
    
                d_loss_real = self.discriminator_CAN.train_on_batch(N_imgs, valid) 

                pre_n = self.discriminator_NOR.predict(C_imgs)
                target = pre_n

                for i in range(target.shape[1]):
                    for j in range(target.shape[2]):
                        if target[0][i][j][0] < thre:
                            target[0][i][j][0]=0
                        else:
                            target[0][i][j][0] = 1
                d_loss_real = self.discriminator_CAN.train_on_batch(C_imgs, target)         
                d_loss_fake = self.discriminator_CAN.train_on_batch(gen_imgs, fake)
                d_loss_NOR = 0.5 * np.add(d_loss_real, d_loss_fake)
                

            # ---------------------
            #  Train Generator
            # ---------------------


            
            g_loss = self.combined.train_on_batch(C_imgs, [valid,valid])

            # Plot the progress
            print ("%d [D loss: %f, acc.: %.2f%%] [G loss: %f, G loss: %f]" % (epoch, d_loss_NOR[0], 100*d_loss_NOR[1], g_loss[0], g_loss[1]))

            # If at save interval => save generated image samples
            if epoch % sample_interval == 0:
                self.sample_images(epoch)

    def sample_images(self, epoch):
        r, c = 5, 5
        #noise = np.random.normal(0, 1, (r * c, self.latent_dim))
        idx_NOR = np.random.randint(0, NOR.shape[0], 25)
        idx_CAN = np.random.randint(0, CAN.shape[0], 25)
        N_imgs = NOR[idx_NOR]
        C_imgs = CAN[0:25]

        gen_imgs = self.generator.predict(C_imgs)

        # Rescale images 0 - 1
        gen_imgs = 0.5 * gen_imgs + 0.5

        fig, axs = plt.subplots(r, c)
        cnt = 0
        for i in range(r):
            for j in range(c):
                axs[i,j].imshow(gen_imgs[cnt][:,:,::-1].reshape(224,224,3) )
                axs[i,j].axis('off')
                cnt += 1
        fig.savefig("/home/auser04/images/%d_0619.png" % epoch)
        plt.close()


if __name__ == '__main__':
    gan = GAN()
    

Please report this to the TensorFlow team. When filing the bug, set the verbosity to 10 (on Linux, `export AUTOGRAPH_VERBOSITY=10`) and attach the full output.
Cause: module 'gast' has no attribute 'Index'
To silence this warning, decorate the function with @tf.autograph.experimental.do_not_convert
Please report this to the TensorFlow team. When filing the bug, set the verbosity to 10 (on Linux, `export AUTOGRAPH_VERBOSITY=10`) and attach the full output.
Cause: module 'gast' has no attribute 'Index'
To silence this warning, decorate the function with @tf.autograph.experimental.do_not_convert
Model: "model"
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
en_img_input (InputLayer)       [(None, 224, 224, 3) 0                                            
________________________________________________________________________________________

Model: "en"
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
en_img_input (InputLayer)       [(None, 224, 224, 3) 0                                            
__________________________________________________________________________________________________
reflection_padding2d_20 (Reflec (None, 230, 230, 3)  0           en_img_input[0][0]               
__________________________________________________________________________________________________
conv2d_32 (Conv2D)              (None, 224, 224, 64) 9408        reflection_padding2d_20[0][0]    
__________________________________________________________________________________________________
instance_normalization_23 (Inst (None, 224, 224, 64) 128         conv2d_32[0][0]                  
_________________________________________________________________________________________________

In [6]:
import tensorflow.keras.backend as K

for th in range(1,5):
    K.clear_session()
    gan = GAN()
    thre = 0.8
    NOR = allNOR[th*5:(th+4)*5]
    CAN = allCAN[th*5:(th+12)*5]
    gan.train(epochs=20000, batch_size=1, sample_interval=100,thre = thre)
    gan.generator.save_weights("5fold_%d_20000" %th)

Model: "model"
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
en_img_input (InputLayer)       [(None, 224, 224, 3) 0                                            
__________________________________________________________________________________________________
reflection_padding2d (Reflectio (None, 230, 230, 3)  0           en_img_input[0][0]               
__________________________________________________________________________________________________
conv2d (Conv2D)                 (None, 224, 224, 64) 9408        reflection_padding2d[0][0]       
__________________________________________________________________________________________________
instance_normalization (Instanc (None, 224, 224, 64) 128         conv2d[0][0]                     
______________________________________________________________________________________________

Model: "en"
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
en_img_input (InputLayer)       [(None, 224, 224, 3) 0                                            
__________________________________________________________________________________________________
reflection_padding2d_20 (Reflec (None, 230, 230, 3)  0           en_img_input[0][0]               
__________________________________________________________________________________________________
conv2d_32 (Conv2D)              (None, 224, 224, 64) 9408        reflection_padding2d_20[0][0]    
__________________________________________________________________________________________________
instance_normalization_23 (Inst (None, 224, 224, 64) 128         conv2d_32[0][0]                  
_________________________________________________________________________________________________

0 [D loss: 0.135413, acc.: 74.49%] [G loss: 0.995559, G loss: 0.883101]
1 [D loss: 0.166583, acc.: 80.36%] [G loss: 0.755830, G loss: 1.135456]
2 [D loss: 0.067032, acc.: 100.00%] [G loss: 0.745255, G loss: 1.020770]
3 [D loss: 0.127977, acc.: 80.36%] [G loss: 0.782998, G loss: 0.819966]
4 [D loss: 0.040199, acc.: 100.00%] [G loss: 0.743270, G loss: 0.742415]
5 [D loss: 0.069587, acc.: 94.13%] [G loss: 0.731697, G loss: 0.445522]
6 [D loss: 0.075318, acc.: 99.49%] [G loss: 0.708201, G loss: 0.274430]
7 [D loss: 0.086281, acc.: 92.60%] [G loss: 0.797060, G loss: 0.220141]
8 [D loss: 0.119488, acc.: 81.63%] [G loss: 0.764298, G loss: 0.198774]
9 [D loss: 0.174188, acc.: 75.77%] [G loss: 0.696055, G loss: 0.284688]
10 [D loss: 0.065196, acc.: 100.00%] [G loss: 0.711347, G loss: 0.280811]
11 [D loss: 0.040956, acc.: 100.00%] [G loss: 0.734592, G loss: 0.212679]
12 [D loss: 0.217114, acc.: 68.88%] [G loss: 0.721883, G loss: 0.089568]
13 [D loss: 0.048720, acc.: 100.00%] [G loss: 0.682787, G

112 [D loss: 0.268791, acc.: 67.09%] [G loss: 0.587973, G loss: 0.136529]
113 [D loss: 0.146622, acc.: 84.69%] [G loss: 0.642114, G loss: 0.031246]
114 [D loss: 0.055029, acc.: 100.00%] [G loss: 0.645825, G loss: 0.046765]
115 [D loss: 0.068227, acc.: 100.00%] [G loss: 0.617392, G loss: 0.098725]
116 [D loss: 0.074196, acc.: 97.45%] [G loss: 0.602621, G loss: 0.056009]
117 [D loss: 0.083074, acc.: 98.98%] [G loss: 0.667237, G loss: 0.029974]
118 [D loss: 0.232423, acc.: 65.31%] [G loss: 0.562196, G loss: 0.023673]
119 [D loss: 0.067298, acc.: 99.74%] [G loss: 0.650046, G loss: 0.066651]
120 [D loss: 0.084972, acc.: 96.68%] [G loss: 0.652939, G loss: 0.117278]
121 [D loss: 0.071450, acc.: 99.74%] [G loss: 0.639203, G loss: 0.098307]
122 [D loss: 0.102523, acc.: 91.58%] [G loss: 0.700926, G loss: 0.152733]
123 [D loss: 0.100876, acc.: 95.92%] [G loss: 0.615031, G loss: 0.074396]
124 [D loss: 0.124495, acc.: 89.29%] [G loss: 0.642092, G loss: 0.039206]
125 [D loss: 0.104201, acc.: 90.31%]

223 [D loss: 0.055978, acc.: 99.23%] [G loss: 0.662009, G loss: 0.154108]
224 [D loss: 0.099418, acc.: 91.58%] [G loss: 0.651266, G loss: 0.166829]
225 [D loss: 0.090106, acc.: 88.78%] [G loss: 0.604617, G loss: 0.167290]
226 [D loss: 0.139894, acc.: 87.76%] [G loss: 0.608651, G loss: 0.188588]
227 [D loss: 0.075568, acc.: 93.88%] [G loss: 0.627714, G loss: 0.241240]
228 [D loss: 0.078852, acc.: 91.07%] [G loss: 0.704218, G loss: 0.172696]
229 [D loss: 0.082237, acc.: 97.19%] [G loss: 0.703461, G loss: 0.303072]
230 [D loss: 0.100805, acc.: 91.33%] [G loss: 0.713205, G loss: 0.252561]
231 [D loss: 0.190864, acc.: 71.94%] [G loss: 0.641567, G loss: 0.256073]
232 [D loss: 0.091500, acc.: 95.41%] [G loss: 0.672054, G loss: 0.148082]
233 [D loss: 0.074240, acc.: 98.98%] [G loss: 0.692103, G loss: 0.118736]
234 [D loss: 0.054228, acc.: 97.19%] [G loss: 0.770084, G loss: 0.151581]
235 [D loss: 0.159039, acc.: 83.93%] [G loss: 0.809631, G loss: 0.079534]
236 [D loss: 0.104997, acc.: 93.62%] [

...

19467 [D loss: 0.003641, acc.: 100.00%] [G loss: 1.081365, G loss: 1.087350]
19468 [D loss: 0.008391, acc.: 100.00%] [G loss: 1.192435, G loss: 2.087056]
19469 [D loss: 0.002823, acc.: 100.00%] [G loss: 0.928354, G loss: 1.511320]
19470 [D loss: 0.034442, acc.: 99.23%] [G loss: 1.279764, G loss: 1.672275]
19471 [D loss: 0.003279, acc.: 100.00%] [G loss: 1.040218, G loss: 1.221057]
19472 [D loss: 0.011738, acc.: 100.00%] [G loss: 1.299924, G loss: 1.079542]
19473 [D loss: 0.005437, acc.: 100.00%] [G loss: 1.130643, G loss: 5.429935]
19474 [D loss: 0.014475, acc.: 100.00%] [G loss: 0.978966, G loss: 3.998489]
19475 [D loss: 0.008136, acc.: 100.00%] [G loss: 1.112376, G loss: 0.867370]
19476 [D loss: 0.016509, acc.: 99.74%] [G loss: 1.163585, G loss: 5.530592]
19477 [D loss: 0.015823, acc.: 100.00%] [G loss: 1.163826, G loss: 1.209426]
19478 [D loss: 0.004508, acc.: 100.00%] [G loss: 1.055400, G loss: 1.363301]
19479 [D loss: 0.004561, acc.: 100.00%] [G loss: 0.992017, G loss: 2.129929]
1

19575 [D loss: 0.005212, acc.: 100.00%] [G loss: 1.004658, G loss: 1.517101]
19576 [D loss: 0.002797, acc.: 100.00%] [G loss: 1.088377, G loss: 2.617411]
19577 [D loss: 0.008680, acc.: 100.00%] [G loss: 1.233392, G loss: 3.926113]
19578 [D loss: 0.028247, acc.: 100.00%] [G loss: 1.032546, G loss: 2.429525]
19579 [D loss: 0.005581, acc.: 100.00%] [G loss: 1.029056, G loss: 4.582156]
19580 [D loss: 0.015306, acc.: 100.00%] [G loss: 1.193147, G loss: 1.234255]
19581 [D loss: 0.006015, acc.: 100.00%] [G loss: 0.972033, G loss: 2.001586]
19582 [D loss: 0.004701, acc.: 100.00%] [G loss: 1.101605, G loss: 1.336411]
19583 [D loss: 0.006465, acc.: 100.00%] [G loss: 1.065568, G loss: 3.416893]
19584 [D loss: 0.008112, acc.: 100.00%] [G loss: 1.132350, G loss: 5.249816]
19585 [D loss: 0.013466, acc.: 100.00%] [G loss: 1.015882, G loss: 1.287925]
19586 [D loss: 0.008617, acc.: 100.00%] [G loss: 1.038524, G loss: 3.472020]
19587 [D loss: 0.012340, acc.: 100.00%] [G loss: 1.176046, G loss: 1.584820]

19683 [D loss: 0.021949, acc.: 98.98%] [G loss: 1.229322, G loss: 1.765785]
19684 [D loss: 0.012837, acc.: 100.00%] [G loss: 1.090442, G loss: 2.290374]
19685 [D loss: 0.007985, acc.: 100.00%] [G loss: 1.023630, G loss: 6.340069]
19686 [D loss: 0.015218, acc.: 98.72%] [G loss: 1.054538, G loss: 1.805443]
19687 [D loss: 0.002225, acc.: 100.00%] [G loss: 0.985753, G loss: 1.110421]
19688 [D loss: 0.004331, acc.: 100.00%] [G loss: 1.127269, G loss: 1.779617]
19689 [D loss: 0.003099, acc.: 100.00%] [G loss: 1.006467, G loss: 4.828287]
19690 [D loss: 0.011994, acc.: 100.00%] [G loss: 1.009062, G loss: 3.640919]
19691 [D loss: 0.008376, acc.: 100.00%] [G loss: 1.001103, G loss: 4.033382]
19692 [D loss: 0.008414, acc.: 100.00%] [G loss: 1.196151, G loss: 1.675878]
19693 [D loss: 0.004508, acc.: 100.00%] [G loss: 1.046831, G loss: 5.976044]
19694 [D loss: 0.002298, acc.: 100.00%] [G loss: 1.013880, G loss: 3.479646]
19695 [D loss: 0.002377, acc.: 100.00%] [G loss: 1.026888, G loss: 4.856898]
1

19791 [D loss: 0.001886, acc.: 100.00%] [G loss: 0.953914, G loss: 3.175369]
19792 [D loss: 0.002715, acc.: 100.00%] [G loss: 1.008593, G loss: 1.902679]
19793 [D loss: 0.004692, acc.: 99.74%] [G loss: 1.094159, G loss: 0.909882]
19794 [D loss: 0.011850, acc.: 100.00%] [G loss: 1.294618, G loss: 1.063228]
19795 [D loss: 0.009798, acc.: 100.00%] [G loss: 0.939216, G loss: 4.045877]
19796 [D loss: 0.021202, acc.: 100.00%] [G loss: 1.242439, G loss: 1.991567]
19797 [D loss: 0.002554, acc.: 100.00%] [G loss: 1.003178, G loss: 5.028671]
19798 [D loss: 0.004090, acc.: 100.00%] [G loss: 0.967699, G loss: 5.174175]
19799 [D loss: 0.004075, acc.: 100.00%] [G loss: 1.041285, G loss: 2.192652]
19800 [D loss: 0.008799, acc.: 100.00%] [G loss: 1.045842, G loss: 8.315714]
19801 [D loss: 0.008770, acc.: 100.00%] [G loss: 1.115344, G loss: 2.807428]
19802 [D loss: 0.003530, acc.: 100.00%] [G loss: 1.016836, G loss: 4.304646]
19803 [D loss: 0.006402, acc.: 99.74%] [G loss: 1.089153, G loss: 1.427715]
1

19899 [D loss: 0.004312, acc.: 100.00%] [G loss: 1.051585, G loss: 4.509322]
19900 [D loss: 0.012983, acc.: 100.00%] [G loss: 1.134364, G loss: 1.596301]
19901 [D loss: 0.003399, acc.: 100.00%] [G loss: 1.029881, G loss: 0.947254]
19902 [D loss: 0.013108, acc.: 99.74%] [G loss: 1.200789, G loss: 1.666875]
19903 [D loss: 0.011549, acc.: 100.00%] [G loss: 1.077216, G loss: 3.479424]
19904 [D loss: 0.013899, acc.: 100.00%] [G loss: 1.103641, G loss: 4.693838]
19905 [D loss: 0.006661, acc.: 100.00%] [G loss: 0.988399, G loss: 6.377989]
19906 [D loss: 0.005516, acc.: 100.00%] [G loss: 1.065247, G loss: 1.892634]
19907 [D loss: 0.003672, acc.: 100.00%] [G loss: 1.099714, G loss: 5.336318]
19908 [D loss: 0.003307, acc.: 100.00%] [G loss: 1.044324, G loss: 7.382433]
19909 [D loss: 0.011852, acc.: 100.00%] [G loss: 1.044694, G loss: 1.584378]
19910 [D loss: 0.017396, acc.: 100.00%] [G loss: 1.183213, G loss: 5.347232]
19911 [D loss: 0.006901, acc.: 100.00%] [G loss: 0.957900, G loss: 4.876128]
